### Objective: To train models with Internal and External datasets. 

IN these experiments, I will train with therapeutic and then train without. Validate on the left out one. 

In [1]:
import mlflow
from mlflow.models import infer_signature

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pathlib import Path
from developability import data as data_
from abnumber import Chain

from sklearn.decomposition import PCA
from tqdm.notebook import tqdm
import tempfile
from dill import dump, load

from developability.utils import ls
from developability.modeling import  *
from developability.model_pipelines import make_pca_pipeline_with_intercept, make_normalize_transformer_pipeline

## retina display
%config InlineBackend.figure_format = 'retina'
pd.set_option('display.max_rows', 999)
pd.set_option('display.max_columns', 999)

import warnings
warnings.filterwarnings("ignore")
# paths 

%load_ext autoreload
%autoreload 2

### Load the data 

In [3]:
data_path = Path(data_.__path__[0])
training_path = data_path / 'train'
data = pd.read_parquet(training_path/'Therapeutic_and_internal_antibodies.parquet')
data.head()

HeparinRRT      Project  HCDR1_APBS_pos  HCDR1_APBS_neg  \
antibody                                                               
adalimumab         0.79  Therapeutic      361.422343     -794.503791   
daclizumab         0.84  Therapeutic     4252.553904        0.000000   
ganitumab          0.79  Therapeutic     1818.147090        0.000000   
vedolizumab        0.54  Therapeutic        0.000000    -2649.100853   
natalizumab        0.54  Therapeutic      972.583337      -97.200479   

             HCDR1_APBS_net  HCDR2_APBS_pos  HCDR2_APBS_neg  HCDR2_APBS_net  \
antibody                                                                      
adalimumab      -433.081449     1555.624126    -4014.715450    -2459.091324   
daclizumab      4252.553904     4452.876492     -904.794295     3548.082197   
ganitumab       1818.147090     6910.914448        0.000000     6910.914448   
vedolizumab    -2649.100853     4492.540426    -5860.854936    -1368.314511   
natalizumab      875.382858    11200.435647     -312.532150    10887.903497   

             HCDR3_APBS_pos  HCDR3_APBS_neg  HCDR3_APBS_net  HFR1_APBS_pos  \
antibody                                                                     
adalimumab      2875.086488     -138.003294     2737.083194    5376.458039   
daclizumab      3911.936888        0.000000     3911.936888   14311.015341   
ganitumab       2961.303964     -484.904947     2476.399018   10333.605343   
vedolizumab        0.000000    -6989.631169    -6989.631169    6391.205916   
natalizumab     5410.511420        0.000000     5410.511420   16469.362126   

             HFR1_APBS_neg  HFR1_APBS_net  HFR2_APBS_pos  HFR2_APBS_neg  \
antibody                                                                  
adalimumab    -1771.257720    3605.200319    2726.475633    -584.411432   
daclizumab     -193.586163   14117.429178    1868.888108     -38.688851   
ganitumab      -525.798048    9807.807295    2872.797423    -281.600949   
vedolizumab    -986.398297    5404.807619    3360.681228       0.000000   
natalizumab    -162.325666   16307.036460    5172.353262       0.000000   

             HFR2_APBS_net  HFR3_APBS_pos  HFR3_APBS_neg  HFR3_APBS_net  \
antibody                                                                  
adalimumab     2142.064200    3398.963679   -1368.871898    2030.091781   
daclizumab     1830.199256    4672.451210    -414.558541    4257.892669   
ganitumab      2591.196475   11761.616999    -147.382398   11614.234601   
vedolizumab    3360.681228    3163.553567   -2239.208472     924.345095   
natalizumab    5172.353262    7039.283850    -181.734569    6857.549282   

             HFR4_APBS_pos  HFR4_APBS_neg  HFR4_APBS_net  LCDR1_APBS_pos  \
antibody                                                                   
adalimumab      905.524940    -973.487817     -67.962877     7088.950311   
daclizumab     1996.455362    -125.736264    1870.719098     2912.056050   
ganitumab       360.371905   -1259.033101    -898.661196     4405.906664   
vedolizumab     306.504321   -1241.789054    -935.284733     3087.786259   
natalizumab    2097.229021    -182.749645    1914.479376     4184.768499   

             LCDR1_APBS_neg  LCDR1_APBS_net  LCDR2_APBS_pos  LCDR2_APBS_neg  \
antibody                                                                      
adalimumab        -2.623292     7086.327019     1842.767512        0.000000   
daclizumab      -214.503158     2697.552891     2848.982419        0.000000   
ganitumab       -170.769361     4235.137303     2334.634695        0.000000   
vedolizumab     -636.602461     2451.183798      509.924516    -1506.710115   
natalizumab     -140.461723     4044.306775     2837.599448        0.000000   

             LCDR2_APBS_net  LCDR3_APBS_pos  LCDR3_APBS_neg  LCDR3_APBS_net  \
antibody                                                                      
adalimumab      1842.767512     3232.607354      -34.553594     3198.053760   
daclizumab      2848.982419    

#### Add internal versus therapeutic label

In [4]:
if 'Source' not in data:
    data.insert(1,'Source', data['Project'].apply(lambda x: 'Therapeutic' if x=='Therapeutic' else 'Internal'))

In [5]:
data.Source.value_counts()

Source
Internal       715
Therapeutic    128
Name: count, dtype: int64

### set up feature sets

In [6]:
def has_number(s): 
    for c in s: 
        if c.isdigit():
            return True
        
    return False

columns = data.columns
tracking_uri = 'http://127.0.0.1:5000'

In [7]:
feature_sets = {'positive_regions': [col for col in columns if col.endswith('pos') and has_number(col)],
                }
for key in feature_sets: 
    feature_sets[key].append('Project')

### Train PCA + onehot

In [7]:
%%capture
experiment_name = 'CompareInternalVersusTherapeutic'
models = ['rf', 'elasticnet']

pipeline_kws = dict(intercept='Project')

sources = data['Source'].unique()

for source in sources: 
    description = f'PCA + OneHot on {source}.'
    train = data.query('Source==@source')

    exp = MLFlowExperiment(train,
                           target='HeparinRRT', 
                           experiment_name=experiment_name,
                           regression=True, 
                           feature_sets = feature_sets, 
                           tracking_uri=tracking_uri,
                           models = models, 
                           pipeline_func = make_pca_pipeline_with_intercept, 
                           pipeline_kws=pipeline_kws,
                           description=description
                           ) 
    
    exp.train_models();

/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 7.444e-01, tolerance: 4.002e-04 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordinate_descent(
/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 7.879e-01, tolerance: 4.240e-04 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using

### Train with normalization 

In [8]:
%%capture
for source in sources: 
    description = f'Normalization + OneHot on {source}.'
    train = data.query('Source==@source')

    exp = MLFlowExperiment(train,
                           target='HeparinRRT', 
                           experiment_name=experiment_name,
                           regression=True, 
                           feature_sets = feature_sets, 
                           tracking_uri=tracking_uri,
                           models = models, 
                           pipeline_func = make_normalize_transformer_pipeline, 
                           pipeline_kws=pipeline_kws,
                           description=description
                           ) 
    
    exp.train_models();

/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.349e+00, tolerance: 4.240e-04 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordinate_descent(
/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.224e+00, tolerance: 3.831e-04 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using

### Train on Internal datasets only. Hold one out. 

In [11]:
%%capture
experiment_name = 'CompareInternalVersusTherapeutic'
models = ['rf', 'elasticnet']

pipeline_kws = dict(intercept='Project')

internal_data=  data.query('Source=="Internal"')
projects=internal_data['Project'].unique()

for project in projects: 
    description = f'Internal PCA + OneHot on {project}.'
    train = internal_data.query('Project!=@project')

    exp = MLFlowExperiment(train,
                           target='HeparinRRT', 
                           experiment_name=experiment_name,
                           regression=True, 
                           feature_sets = feature_sets, 
                           tracking_uri=tracking_uri,
                           models = models, 
                           pipeline_func = make_pca_pipeline_with_intercept, 
                           pipeline_kws=pipeline_kws,
                           description=description
                           ) 
    
    exp.train_models();


for project in projects: 
    description = f'Internal Normalization + OneHot on {project}.'
    train = internal_data.query('Project!=@project')

    exp = MLFlowExperiment(train,
                           target='HeparinRRT', 
                           experiment_name=experiment_name,
                           regression=True, 
                           feature_sets = feature_sets, 
                           tracking_uri=tracking_uri,
                           models = models, 
                           pipeline_func = make_normalize_transformer_pipeline, 
                           pipeline_kws=pipeline_kws,
                           description=description
                           ) 
    
    exp.train_models();

/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.728e-01, tolerance: 1.040e-04 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordinate_descent(
/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.509e-01, tolerance: 9.974e-05 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using

### Comment: 
Above I trained models to compare between datasets. 

### Train model with all datasets.

Previous extensive analysis indicates that the best model overall is an elasticnet with all internal and therapeutic, using normalization + one_hot. 
I am training that model here. 

In [10]:
%%capture
experiment_name = 'CompareInternalVersusTherapeutic'

description = f'Normalization + OneHot Trained on Therapeutic + Internal for prod'
train = data
pipeline_kws = dict(intercept='Project')
models = ['elasticnet']


exp = MLFlowExperiment(train,
                       target='HeparinRRT', 
                       experiment_name=experiment_name,
                       regression=True, 
                       feature_sets = feature_sets, 
                       tracking_uri=tracking_uri,
                       models = models, 
                       pipeline_func = make_normalize_transformer_pipeline, 
                       pipeline_kws=pipeline_kws,
                       description=description
                       ) 

exp.train_models();

/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.022e+00, tolerance: 2.166e-03 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordinate_descent(
/home/crivera/miniforge3/envs/surface/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.505e+00, tolerance: 2.030e-03 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using

<bound method MLFlowExperiment.train_models of <developability.modeling.MLFlowExperiment object at 0x7f48902627d0>>